In [120]:
___Author___='LumberJack Jyss'

In [121]:
print('Global Optimized LumberJack Equities Method\n°OoO_FOREX_Oo0°\nLumberJack Jyss 5779(c)')

Global Optimized LumberJack Equities Method
°OoO_FOREX_Oo0°
LumberJack Jyss 5779(c)


In [122]:
#data_history = []

In [149]:
print('Importation des librairies...')
import numpy
import pandas as pd
import matplotlib.pyplot as plt
from pandas import read_csv
import math
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error
print('Librairies importées')

Importation des librairies...
Librairies importées


In [150]:
# convert an array of values into a dataset matrix
def create_dataset(dataset, look_back=1):
	dataX, dataY = [], []
	for i in range(len(dataset)-look_back-1):
		a = dataset[i:(i+look_back), 0]
		dataX.append(a)
		dataY.append(dataset[i + look_back, 0])
	return numpy.array(dataX), numpy.array(dataY)

In [151]:
# fix random seed for reproducibility
numpy.random.seed(7)
# load the dataset
dataframe = read_csv("1_MIN_ALL.txt", index_col=0, sep = ' ')
dataframe['Vol'] = dataframe['Vol'].str.replace("'", '')
dataframe = dataframe.tail(50000)
dataframe.head()

/Users/YTsBaCh/Applications/anaconda3/envs/LumberJack/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3049: DtypeWarning:

Columns (8) have mixed types. Specify dtype option on import or set low_memory=False.



Per      Date    Time     Open     High      Low    Close   Vol
Ticker                                                                 
EURUSD    1  20170731  162000  1.17385  1.17399  1.17370  1.17396  1011
EURUSD    1  20170731  162100  1.17388  1.17421  1.17378  1.17420  1276
EURUSD    1  20170731  162200  1.17417  1.17420  1.17389  1.17407  1354
EURUSD    1  20170731  162300  1.17410  1.17425  1.17390  1.17420  1484
EURUSD    1  20170731  162400  1.17419  1.17421  1.17390  1.17410  1484

In [152]:
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
cf.go_offline()
dataframe.iplot(x='Time',y=['Close','High','Low'])

In [153]:
dataframe = dataframe[['Close']]
dataframe = dataframe.reset_index(drop = True)
dataset = dataframe.values
dataset = dataset.astype('float32')
dataframe.head()

Close
0  1.17396
1  1.17420
2  1.17407
3  1.17420
4  1.17410

In [154]:
# normalize the dataset
scaler = MinMaxScaler(feature_range=(0, 1))
dataset = scaler.fit_transform(dataset)
# split into train and test sets
train_size = int(len(dataset) * 0.67)
test_size = len(dataset) - train_size
train, test = dataset[0:train_size,:], dataset[train_size:len(dataset),:]

In [213]:
# reshape into X=t and Y=t+1
look_back = 5
trainX, trainY = create_dataset(train, look_back)
testX, testY = create_dataset(test, look_back)

# reshape input to be [samples, time steps, features]
trainX = numpy.reshape(trainX, (trainX.shape[0], 1, trainX.shape[1]))
testX = numpy.reshape(testX, (testX.shape[0], 1, testX.shape[1]))

In [ ]:
# create and fit the LSTM network
epochs_custom = 20
model = Sequential()
model.add(LSTM(50, input_shape=(1, look_back)))
model.add(Dense(1))
model.compile(loss='mean_squared_error', optimizer='adam')
model.fit(trainX, trainY, epochs=epochs_custom, batch_size=1, verbose=1)

Epoch 1/20
33494/33494 [==============================] - 305s 9ms/sample - loss: 1.6913e-04
Epoch 2/20
33494/33494 [==============================] - 297s 9ms/sample - loss: 3.7051e-05
Epoch 3/20
33494/33494 [==============================] - 293s 9ms/sample - loss: 3.2959e-05
Epoch 4/20
33494/33494 [==============================] - 262s 8ms/sample - loss: 3.0298e-05
Epoch 5/20
33494/33494 [==============================] - 214s 6ms/sample - loss: 2.8136e-05
Epoch 6/20
33494/33494 [==============================] - 197s 6ms/sample - loss: 2.7091e-05
Epoch 7/20
28619/33494 [========================>.....] - ETA: 28s - loss: 2.6007e-05

In [ ]:
# make predictions
trainPredict = model.predict(trainX)
testPredict = model.predict(testX)

In [ ]:
# invert predictions
trainPredict = scaler.inverse_transform(trainPredict)
trainY = scaler.inverse_transform([trainY])
testPredict = scaler.inverse_transform(testPredict)
testY = scaler.inverse_transform([testY])

In [ ]:
# calculate root mean squared error
trainScore = math.sqrt(mean_squared_error(1000*(trainY[0]), 1000*trainPredict[:,0]))
print('Train Score: %.2f RMSE' % (trainScore))
testScore = math.sqrt(mean_squared_error(1000*testY[0], 1000*testPredict[:,0]))
print('Test Score: %.2f RMSE' % (testScore))

In [ ]:
# shift train predictions for plotting
trainPredictPlot = numpy.empty_like(dataset)
trainPredictPlot[:, :] = numpy.nan
trainPredictPlot[look_back:len(trainPredict)+look_back, :] = trainPredict
# shift test predictions for plotting
testPredictPlot = numpy.empty_like(dataset)
testPredictPlot[:, :] = numpy.nan
testPredictPlot[len(trainPredict)+(look_back*2)+1:len(dataset)-1, :] = testPredict
# plot baseline and predicZtions
plt.figure(figsize=(16,6),dpi=200)
plt.plot(scaler.inverse_transform(dataset),label='Inverse Scaler')
plt.plot(trainPredictPlot,label='Train predict')
plt.plot(testPredictPlot,label = 'Test Predict')
plt.legend()
plt.show()

In [ ]:
print(model.summary())

In [ ]:
Predictions = []
Real = []
result = []
error= []

for i in range(0,len(testPredict)):
    if scaler.inverse_transform(testX[i])[0][look_back - 1] - testPredict[i] < 0:
        Predictions.append('Sell')
    else:
        Predictions.append('Buy')
    
    if scaler.inverse_transform(testX[i])[0][look_back - 1] - testY[0][i] < 0:
        Real.append('Sell')
    else:
        Real.append('Buy')
    
    if Predictions[i] == Real[i]:
        result.append(True)
    else:
        result.append(False)
    
    error.append(math.sqrt((scaler.inverse_transform(testX[i])[0][look_back - 1] - testPredict[i])*
            (scaler.inverse_transform(testX[i])[0][look_back - 1] - testPredict[i])))

In [ ]:
freq = pd.DataFrame({'col':result})
freq.describe()

In [ ]:
mse = pd.DataFrame({'col':error})
mse.describe()

In [ ]:
freq.describe()['col'][3]/freq.describe()['col'][0]

In [ ]:
accuracy = freq.describe()['col'][3]/freq.describe()['col'][0]
data_history.append([round(accuracy*100),epochs_custom,look_back,testScore,trainScore,mse.describe()['col'][3]])
df = pd.DataFrame(data_history,columns=['accuracy','epochs','look_back','trainScore','testScore','mse'])

In [ ]:
df.head()

In [ ]:
#testPredict[:,0].shape,testY[:,1].shape
testY[0,:]

In [ ]:
final_cut = pd.DataFrame()
final_cut['Actual'] = testY[0,:]
final_cut['Prediction'] = testPredict[:,0]
final_cut['Delat'] = (final_cut['Actual'] - final_cut['Prediction'])
final_cut.tail(15)